# Description
In this notebook, we will perform software project cost prediction using Random Forest Regressor. We use the regressor because our output values cannot be described as classes. Our dataset has as output numeric values.

In [1]:
import numpy as np
from sklearn import preprocessing
from scipy.io import arff
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split
from sklearn import preprocessing
from sklearn.model_selection import KFold,cross_val_score
from sklearn.model_selection import GridSearchCV,RandomizedSearchCV

# Info about the train dataset

The dataset has datat collected from personal and work-related projects. It is written following the style of the COCOMO81 dataset, which is a dataset containing information about NASA projects. For the validation dataset set, we will use COCOMO81.

## Details about the COCMO model

The COCOMO software cost model measures effort in calendar months of 152 hours (and includes development and management hours).
COCOMO assumes that the effort grows more than linearly on software size.
          
The effort multipliers fall into three groups: those that are positively correlated to more effort; those that are negatively correlated to more effort; and a third group containing just schedule information. In COCOMO~I, "sced" has a U-shaped correlation to effort; i.e. giving programmers either too much or too little time to develop a system can be detrimental.



The standard numeric values of the effort multipliers are:

|multiplier meaning| multiplier      | very low | low | nominal | high | very high | extra high | productivity range|
|:-----| :-----------: | ----------- | ----------- | ----------- | ----------- | ----------- | ----------- | :-----------: |
| analysts capability| acap| 1.46  | 1.19  |  1.00   |	0.86  | 0.71   |  |   2.06 |
| programmers capability| pcap| 1.42  | 1.17  |  1.00   |	0.86  | 0.70   |  |   1.67 |
| application experience| aexp| 1.29  | 1.13  |  1.00   |	0.91  | 0.82   |  |   1.57 |
| modern programing practices| modp| 1.24  | 1.10  |  1.00   |	0.91  | 0.82   |  |   1.34 |
| use of  software tool| tool| 1.24  | 1.10  |  1.00   |	0.91  | 0.83   |  |   1.49 |
| virtual machine experience| vexp| 1.21  | 1.10  |  1.00   |	0.90  |    |  |   1.34 |
| language experience| lexp| 1.14  | 1.07  |  1.00   |	0.95  |    |  |   1.20 |
| schedule constraint| sced| 1.23  | 1.08  |  1.00   |	1.04  | 0.20   |  |   e |
| main memory constraint| stor|   |   |  1.00   |	1.06  | 1.21   | 1.56 |   -1.21 |
| data base size| data|   | 0.94  |  1.00   |	1.08  | 1.16   |  |   -1.23 |
| time constraint for cpu| time|  | 0.87  |  1.00   |	1.11  | 1.3   |  1.66|   -1.3 |
| turnaround time| turn|   | 0.87  |  1.00   |	1.07  | 1.15   |  |   -1.32 |
| machine volatility| virt|   | 0.87 |  1.00   |	1.15  | 1.3   |  |   -1.48 |
| process complexity| cplx| 0.7  | 0.85  |  1.00   |	1.15  | 1.30   | 1.65 |   -1.86 |
| required software reliability| rely| 0.75  | 0.88  |  1.00   |	1.15  | 1.40   |  |   -1.87 |



These were learnt by Barry Boehm after a regression analysis of the projects in the COCOMO I data set and these are the values that will be used in the collection of the dataset.

The last column of the above table shows max(E)/min(EM) and shows the overall effect of a single effort multiplier. For example, increasing "acap" (analyst experience) from very low to very high will most decrease effort while increasing "rely" (required reliability) from very low to very high will most increase effort.

So, for the multiplers that have a positive productivity range, their increase will mean a decrease in effort, and the opposite goes for those with negative productivity ranges.

# The dataset

In [2]:
dataset = arff.loadarff(open('/Users/neniscamaria/Documents/Master/an 2/semestru 1/ai in se/train.arff'))

In [3]:
data = pd.DataFrame(dataset[0])
data.head()

rely  data  cplx  time  stor  virt  turn  acap  aexp  pcap  vexp  lexp  \
0  0.88  1.16  0.70   1.0  1.06  1.15  1.07  1.19  1.13  1.17   1.1  1.00   
1  0.88  1.16  0.85   1.0  1.06  1.00  1.07  1.00  0.91  1.00   0.9  0.95   
2  1.00  1.16  0.85   1.0  1.00  0.87  0.94  0.86  0.82  0.86   0.9  0.95   
3  0.75  1.16  0.70   1.0  1.00  0.87  1.00  1.19  0.91  1.42   1.0  0.95   
4  0.88  0.94  1.00   1.0  1.00  0.87  1.00  1.00  1.00  0.86   0.9  0.95   

   modp  tool  sced  loc  actual  
0  1.24  1.10  1.04  1.1     1.0  
1  1.10  1.00  1.00  2.0     1.0  
2  0.91  0.91  1.00  1.3     1.0  
3  1.24  1.00  1.04  1.6     1.0  
4  1.24  1.00  1.00  2.2     3.0

# Preparing the data
Extract the class attribute values for the test and train data sets.



In [4]:
Y = data['actual']
X = data.drop('actual', axis=1)

Split the custom dataset in train/test with 70/30.

In [5]:
X_train, X_test, y_train, y_test = train_test_split(
    X, Y, test_size=0.30, random_state=42)

Encode the labels

In [6]:
lab_enc = preprocessing.LabelEncoder()
training_scores_encoded = lab_enc.fit_transform(y_train)

# Performance metrics
The value of an effort predictor can be reported many ways including MMRE and PRED(N). MMRE and PRED are computed from the relative error, or RE, which is the relative size of the difference between the actual and estimated value:

$RE_{i} = \frac{estimate_{i} - actual_{i}}{actual_{i}}$

Given a data set of of size "D", a "Train"ing set of size "(X=|Train|) <= D", and a "test" set of size "T=D-|Train|", then the mean magnitude of the relative error, or MMRE, is the percentage of the absolute values of the relative errors, averaged over the "T" items in the "Test" set; i.e.

$MRE_{i}  = abs(RE_{i})$

$MMRE_{i} = \frac{100}{T}*( MRE_{1} + MRE_{2} + ... + MRE_{T})$

PRED(N) reports the average percentage of estimates that were within N% of the actual values:

```python
count = 0

for(i=1;i<=T;i++) do if MRE.i <= N/100 then count++ fi done

PRED(N) = 100/T * count
```

For example, e.g. PRED(30)=50% means that half the estimates are within 30% of the actual.  Shepperd and Schofield comment that "MMRE is fairly conservative with a bias against overestimates while Pred(25) will identify those prediction systems that are generally accurate but occasionally wildly inaccurate".


In [7]:
def computeRE(Y_pred):
    return np.absolute(y_test-Y_pred)

In [8]:
def computeMRE(diff):
    return diff/y_test

In [9]:
def computeMMRE(diff):
    return np.mean(computeMRE(diff))

In [10]:
def computeMdMRE(diff):
    return np.median(computeMRE(diff))

In [11]:
def computePred(diff):
    MRE = computeMRE(diff)
    P=MRE[MRE<.25]
    return (P.size/MRE.size) * 100

In [12]:
def computeMetrics(Y_pred):
    RE=computeRE(Y_pred)
    MMRE = computeMMRE(RE)
    MdMRE = computeMdMRE(RE)
    Pred = computePred(RE)
    
    return MMRE, MdMRE, Pred

# Hyperparameter tuning

We use 2 different methods to determine the optimal values for our random forest model. For both methods, we will use the same parameter combinations, as defined below.

In [20]:
params_grd={'bootstrap': [True, False],
 'max_depth': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100, None],
 'max_features': [1,2,3,4,5,6],
 'min_samples_leaf': [1, 2, 4],
 'min_samples_split': [2, 5, 10],
 'n_estimators': [200, 400, 600, 800, 1000]}

## Tuning using GridSearchCV

In [21]:
clf= RandomForestRegressor()
grd_search=GridSearchCV(estimator = clf, param_grid = params_grd, 
                          cv = 10, n_jobs = -1, verbose = 2)

grd_search.fit(X_train, training_scores_encoded)

Fitting 10 folds for each of 5940 candidates, totalling 59400 fits
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=200; total time=   0.1s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=400; total time=   0.2s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=600; total time=   0.4s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=600; total time=   0.3s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=800; total time=   0.5s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=1000; total time=   0.6s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=5, n_estimators=200; total time=   0.1s
[

[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=200; total time=   0.1s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=400; total time=   0.2s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=400; total time=   0.2s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=600; total time=   0.4s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=800; total time=   0.5s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=1000; total time=   0.6s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=5, n_estimators=200; total time=   0.1s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_l

[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=200; total time=   0.1s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=400; total time=   0.2s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=600; total time=   0.4s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=800; total time=   0.5s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=800; total time=   0.5s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=1000; total time=   0.6s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=5, n_estimators=400; total time=   0.2s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_l

[CV] END bootstrap=True, max_depth=10, max_features=2, min_samples_leaf=1, min_samples_split=5, n_estimators=600; total time=   0.4s
[CV] END bootstrap=True, max_depth=10, max_features=2, min_samples_leaf=1, min_samples_split=5, n_estimators=800; total time=   0.5s
[CV] END bootstrap=True, max_depth=10, max_features=2, min_samples_leaf=1, min_samples_split=5, n_estimators=1000; total time=   0.6s
[CV] END bootstrap=True, max_depth=10, max_features=2, min_samples_leaf=1, min_samples_split=5, n_estimators=1000; total time=   0.7s
[CV] END bootstrap=True, max_depth=10, max_features=2, min_samples_leaf=1, min_samples_split=10, n_estimators=400; total time=   0.3s
[CV] END bootstrap=True, max_depth=10, max_features=2, min_samples_leaf=1, min_samples_split=10, n_estimators=600; total time=   0.4s
[CV] END bootstrap=True, max_depth=10, max_features=2, min_samples_leaf=1, min_samples_split=10, n_estimators=800; total time=   0.5s
[CV] END bootstrap=True, max_depth=10, max_features=2, min_sampl

[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=200; total time=   0.1s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=400; total time=   0.2s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=600; total time=   0.4s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=600; total time=   0.4s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=800; total time=   0.5s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, n_estimators=1000; total time=   0.6s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=5, n_estimators=200; total time=   0.1s
[CV] END bootstrap=True, max_depth=10, max_features=1, min_samples_l

...

[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=2, min_samples_split=5, n_estimators=600; total time=   0.3s
[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=2, min_samples_split=5, n_estimators=600; total time=   0.3s
[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=2, min_samples_split=5, n_estimators=800; total time=   0.3s
[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=2, min_samples_split=5, n_estimators=1000; total time=   0.4s
[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=2, min_samples_split=10, n_estimators=200; total time=   0.1s
[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=2, min_samples_split=10, n_estimators=200; total time=   0.1s
[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=2, min_samples_split=10, n_estimators=400; total time=   0.2s
[CV] END bootstrap=False, max_depth=100, max_featur

[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=2, min_samples_split=5, n_estimators=1000; total time=   0.4s
[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=2, min_samples_split=5, n_estimators=1000; total time=   0.4s
[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=2, min_samples_split=10, n_estimators=400; total time=   0.2s
[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=2, min_samples_split=10, n_estimators=600; total time=   0.3s
[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=2, min_samples_split=10, n_estimators=800; total time=   0.3s
[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=2, min_samples_split=10, n_estimators=1000; total time=   0.4s
[CV] END bootstrap=False, max_depth=100, max_features=1, min_samples_leaf=4, min_samples_split=2, n_estimators=200; total time=   0.1s
[CV] END bootstrap=False, max_depth=100, max_fea

[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=1, min_samples_split=10, n_estimators=1000; total time=   0.4s[CV] END bootstrap=False, max_depth=100, max_features=2, min_samples_leaf=2, min_samples_split=5, n_estimators=400; total time=   0.2s
[CV] END bootstrap=False, max_depth=100, max_features=2, min_samples_leaf=2, min_samples_split=5, n_estimators=600; total time=   0.3s
[CV] END bootstrap=False, max_depth=100, max_features=2, min_samples_leaf=2, min_samples_split=5, n_estimators=600; total time=   0.3s
[CV] END bootstrap=False, max_depth=100, max_features=2, min_samples_leaf=2, min_samples_split=5, n_estimators=800; total time=   0.3s
[CV] END bootstrap=False, max_depth=100, max_features=2, min_samples_leaf=2, min_samples_split=5, n_estimators=1000; total time=   0.5s
[CV] END bootstrap=False, max_depth=100, max_features=2, min_samples_leaf=2, min_samples_split=10, n_estimators=200; total time=   0.1s
[CV] END bootstrap=False, max_depth=100, max_featur

[CV] END bootstrap=False, max_depth=100, max_features=2, min_samples_leaf=4, min_samples_split=2, n_estimators=800; total time=   0.4s
[CV] END bootstrap=False, max_depth=100, max_features=2, min_samples_leaf=4, min_samples_split=2, n_estimators=1000; total time=   0.4s
[CV] END bootstrap=False, max_depth=100, max_features=2, min_samples_leaf=4, min_samples_split=5, n_estimators=400; total time=   0.1s
[CV] END bootstrap=False, max_depth=100, max_features=2, min_samples_leaf=4, min_samples_split=5, n_estimators=400; total time=   0.2s
[CV] END bootstrap=False, max_depth=100, max_features=2, min_samples_leaf=4, min_samples_split=5, n_estimators=600; total time=   0.3s
[CV] END bootstrap=False, max_depth=100, max_features=2, min_samples_leaf=4, min_samples_split=5, n_estimators=800; total time=   0.3s
[CV] END bootstrap=False, max_depth=100, max_features=2, min_samples_leaf=4, min_samples_split=5, n_estimators=1000; total time=   0.4s
[CV] END bootstrap=False, max_depth=100, max_features

GridSearchCV(cv=10, estimator=RandomForestRegressor(), n_jobs=-1,
             param_grid={'bootstrap': [True, False],
                         'max_depth': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100,
                                       None],
                         'max_features': [1, 2, 3, 4, 5, 6],
                         'min_samples_leaf': [1, 2, 4],
                         'min_samples_split': [2, 5, 10],
                         'n_estimators': [200, 400, 600, 800, 1000]},
             verbose=2)

Train and test the model

In [22]:
best_grid = grd_search.best_estimator_

Y_pred=best_grid.predict(X_test)

Evaluate the model

In [23]:
MMRE, MdMRE, Pred = computeMetrics(Y_pred)
print(MMRE)
print(MdMRE)
print(Pred)

0.41082108213518836
0.35241071428571413
31.57894736842105


In [24]:
grd_search.best_params_

{'bootstrap': False,
 'max_depth': 30,
 'max_features': 2,
 'min_samples_leaf': 4,
 'min_samples_split': 5,
 'n_estimators': 200}

## Tuning using Random Hyperparameter Grid

In [26]:
clf= RandomForestRegressor()
random_grd_search=RandomizedSearchCV(estimator = clf, param_distributions = params_grd, n_iter = 80, cv = 10, 
                              verbose=2, random_state=42, n_jobs = -1)
random_grd_search.fit(X_train, training_scores_encoded)


Fitting 10 folds for each of 80 candidates, totalling 800 fits


RandomizedSearchCV(cv=10, estimator=RandomForestRegressor(), n_iter=80,
                   n_jobs=-1,
                   param_distributions={'bootstrap': [True, False],
                                        'max_depth': [10, 20, 30, 40, 50, 60,
                                                      70, 80, 90, 100, None],
                                        'max_features': [1, 2, 3, 4, 5, 6],
                                        'min_samples_leaf': [1, 2, 4],
                                        'min_samples_split': [2, 5, 10],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000]},
                   random_state=42, verbose=2)


[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=2, n_estimators=200; total time=   0.1s
[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=2, n_estimators=200; total time=   0.1s
[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=2, n_estimators=200; total time=   0.1s
[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=2, n_estimators=400; total time=   0.2s
[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=2, n_estimators=600; total time=   0.3s
[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=2, n_estimators=600; total time=   0.3s
[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=2, n_estimators=800; total time=   0.4s
[CV] END bootstrap=False, max_depth=None, max_f

[CV] END bootstrap=False, max_depth=None, max_features=3, min_samples_leaf=4, min_samples_split=5, n_estimators=800; total time=   0.3s
[CV] END bootstrap=False, max_depth=None, max_features=3, min_samples_leaf=4, min_samples_split=5, n_estimators=1000; total time=   0.4s
[CV] END bootstrap=False, max_depth=None, max_features=3, min_samples_leaf=4, min_samples_split=5, n_estimators=1000; total time=   0.4s
[CV] END bootstrap=False, max_depth=None, max_features=3, min_samples_leaf=4, min_samples_split=10, n_estimators=600; total time=   0.2s
[CV] END bootstrap=False, max_depth=None, max_features=3, min_samples_leaf=4, min_samples_split=10, n_estimators=600; total time=   0.2s
[CV] END bootstrap=False, max_depth=None, max_features=3, min_samples_leaf=4, min_samples_split=10, n_estimators=800; total time=   0.3s
[CV] END bootstrap=False, max_depth=None, max_features=3, min_samples_leaf=4, min_samples_split=10, n_estimators=1000; total time=   0.4s
[CV] END bootstrap=False, max_depth=None,

In [27]:
best_grid_random = random_grd_search.best_estimator_

Y_pred=best_grid_random.predict(X_test)

In [28]:
MMRE, MdMRE, Pred = computeMetrics(Y_pred)
print(MMRE)
print(MdMRE)
print(Pred)

0.4244157560206433
0.4057215608465611
31.57894736842105


In [29]:
random_grd_search.best_params_

{'n_estimators': 600,
 'min_samples_split': 2,
 'min_samples_leaf': 4,
 'max_features': 3,
 'max_depth': 70,
 'bootstrap': False}

[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=5, n_estimators=800; total time=   0.4s
[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=5, n_estimators=1000; total time=   0.4s
[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=10, n_estimators=400; total time=   0.2s
[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=10, n_estimators=400; total time=   0.2s
[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=10, n_estimators=600; total time=   0.3s
[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=10, n_estimators=800; total time=   0.4s
[CV] END bootstrap=False, max_depth=None, max_features=4, min_samples_leaf=2, min_samples_split=10, n_estimators=1000; total time=   0.4s
[CV] END bootstrap=False, max_depth=None,

## Observations:
### Random forest regressor + GridSearchCV
MMRE = 0.41082108213518836

MdRE = 0.35241071428571413

PRED(25) = 31.57894736842105


### Random forest regressor + RandomizedSearchCV
MMRE = 0.4244157560206433

MdMRE = 0.4057215608465611

PRED(25) = 31.57894736842105

# Validating on real world Dataset 
## The data

In [30]:
validation_dataset = arff.loadarff(open('/Users/neniscamaria/Documents/Master/an 2/semestru 1/ai in se/test.arff'))

In [31]:
validation_data = pd.DataFrame(validation_dataset[0])
validation_data.head()

rely  data  cplx  time  stor  virt  turn  acap  aexp  pcap  vexp  lexp  \
0  1.40  1.08  1.00  1.48  1.56  1.15  1.07  0.86  0.82  0.86   1.1  1.07   
1  0.88  1.08  0.85  1.00  1.00  1.00  1.00  0.71  0.82  1.00   1.0  1.00   
2  1.40  1.08  1.30  1.48  1.56  1.15  0.94  0.86  0.82  0.86   0.9  1.00   
3  1.15  1.08  1.00  1.06  1.00  1.00  0.87  1.00  1.00  1.00   1.0  1.00   
4  0.75  0.94  1.30  1.06  1.21  1.15  1.00  1.00  0.91  1.00   1.1  1.00   

   modp  tool  sced    loc  actual  
0  1.00  1.00  1.00   62.0  1063.0  
1  1.10  1.10  1.00  390.0   702.0  
2  0.91  0.91  1.00   42.0   605.0  
3  0.91  1.10  1.23   23.0   230.0  
4  1.24  1.24  1.00   13.0    82.0

Preparing the data

In [32]:
Y = validation_data['actual']
X = validation_data.drop('actual', axis=1)

In [33]:
X_train, X_test, y_train, y_test = train_test_split(
    X, Y, test_size=0.30, random_state=42)

In [34]:
lab_enc = preprocessing.LabelEncoder()
training_scores_encoded = lab_enc.fit_transform(y_train)

## Random forest regressor + GridSearchCV

In [35]:
best_grid = grd_search.best_estimator_

Y_pred=best_grid.predict(X_test)

In [36]:
MMRE, MdMRE, Pred = computeMetrics(Y_pred)
print(MMRE)
print(MdMRE)
print(Pred)

0.9724146718500501
0.9915039864569681
0.0


Random forest regressot + RandomizedSearchCV

In [37]:
best_grid_random = random_grd_search.best_estimator_

Y_pred=best_grid_random.predict(X_test)

In [38]:
MMRE, MdMRE, Pred = computeMetrics(Y_pred)
print(MMRE)
print(MdMRE)
print(Pred)

0.9729795708006295
0.9909982464443473
0.0


## Observations
On our custom dataset the regressor performed rather poorly. However, on the real world validation dataset, the model had excelent performance.